# ML Pipeline Preparation
### 1. Import libraries and load data from database.
- Import Python libraries
- Load dataset from database with [`read_sql_table`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_sql_table.html)
- Define feature and target variables X and Y

In [1]:
# import libraries
import pandas as pd
import numpy as np
import matplotlib as plt
from sqlalchemy import create_engine
import re
import nltk
nltk.download(['punkt','stopwords','wordnet', 'averaged_perceptron_tagger'])
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords

from sklearn.metrics import confusion_matrix
from sklearn.model_selection import GridSearchCV
from sklearn.multioutput import MultiOutputClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer

[nltk_data] Downloading package punkt to /Users/jaywang/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/jaywang/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/jaywang/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/jaywang/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [2]:
# load data from database
engine = create_engine('sqlite:///Disaster_response_data.db')
df = pd.read_sql('SELECT * FROM Disaster_data', engine)
df.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  related  \
0  Un front froid se retrouve sur Cuba ce matin. ...  direct        1   
1                 Cyclone nan fini osinon li pa fini  direct        1   
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct        1   
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct        1   
4  facade ouest d Haiti et le reste du pays aujou...  direct        1   

   request  offer  aid_related  medical_help  medical_products  ...  \
0        0      0            0             0                 0  ...   
1        0      0            1             0                 0  ...   
2        0      0            0             0                 0  ...   
3        1      0            1             0                 1  ...   
4        0      0            0             0                 0  ...   

   aid_centers  other_infrastructure  weather_related  floods  storm  fire  \
0            0                     0                0       0      0     0   
1            0                     0                1       0      1     0   
2            0                     0                0       0      0     0   
3            0                     0                0       0      0     0   
4            0                     0                0       0      0     0   

   earthquake  cold  other_weather  direct_report  
0           0     0              0              0  
1           0     0              0              0  
2           0     0              0              0  
3           0     0              0              0  
4           0     0              0              0  

[5 rows x 40 columns]

In [12]:
X = df['message']
y = df.iloc[:,4:]

In [13]:
X.head()

0    Weather update - a cold front from Cuba that c...
1              Is the Hurricane over or is it not over
2                      Looking for someone but no name
3    UN reports Leogane 80-90 destroyed. Only Hospi...
4    says: west side of Haiti, rest of the country ...
Name: message, dtype: object

In [14]:
y.head()

related  request  offer  aid_related  medical_help  medical_products  \
0        1        0      0            0             0                 0   
1        1        0      0            1             0                 0   
2        1        0      0            0             0                 0   
3        1        1      0            1             0                 1   
4        1        0      0            0             0                 0   

   search_and_rescue  security  military  child_alone  ...  aid_centers  \
0                  0         0         0            0  ...            0   
1                  0         0         0            0  ...            0   
2                  0         0         0            0  ...            0   
3                  0         0         0            0  ...            0   
4                  0         0         0            0  ...            0   

   other_infrastructure  weather_related  floods  storm  fire  earthquake  \
0                     0                0       0      0     0           0   
1                     0                1       0      1     0           0   
2                     0                0       0      0     0           0   
3                     0                0       0      0     0           0   
4                     0                0       0      0     0           0   

   cold  other_weather  direct_report  
0     0              0              0  
1     0              0              0  
2     0              0              0  
3     0              0              0  
4     0              0              0  

[5 rows x 36 columns]

### 2. Write a tokenization function to process your text data

In [6]:
def tokenize(text):
    # Normalize
    text = re.sub(r'[^a-zA-Z0-9]', ' ', text.lower())
    # Tokenization
    words = word_tokenize(text)
    # Remove stop words
    words = [w for w in words if w not in stopwords.words('english')]
    # Lemmatize
    lemmatizer = [WordNetLemmatizer().lemmatize(w) for w in words]
    return lemmatizer

tokenize(X[0])

['weather', 'update', 'cold', 'front', 'cuba', 'could', 'pas', 'haiti']

In [7]:
for message in X:
    tokens = tokenize(message)
    print(message)
    print(tokens,'\n')

Weather update - a cold front from Cuba that could pass over Haiti
['weather', 'update', 'cold', 'front', 'cuba', 'could', 'pas', 'haiti'] 

Is the Hurricane over or is it not over
['hurricane'] 

Looking for someone but no name
['looking', 'someone', 'name'] 

UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs supplies desperately.
['un', 'report', 'leogane', '80', '90', 'destroyed', 'hospital', 'st', 'croix', 'functioning', 'need', 'supply', 'desperately'] 

says: west side of Haiti, rest of the country today and tonight
['say', 'west', 'side', 'haiti', 'rest', 'country', 'today', 'tonight'] 

Information about the National Palace-
['information', 'national', 'palace'] 

Storm at sacred heart of jesus
['storm', 'sacred', 'heart', 'jesus'] 

Please, we need tents and water. We are in Silo, Thank you!
['please', 'need', 'tent', 'water', 'silo', 'thank'] 

I would like to receive the messages, thank you
['would', 'like', 'receive', 'message', 'thank'] 

I am 

Im asking a general prayer for the country of Haiti.
['im', 'asking', 'general', 'prayer', 'country', 'haiti'] 

We are at KF Marotiere 85, we have food and water shortage, please send food for us.
['kf', 'marotiere', '85', 'food', 'water', 'shortage', 'please', 'send', 'food', 'u'] 

I'm listening to you at Miraguan we asking the government to take change because one gallon gas is 80.
['listening', 'miraguan', 'asking', 'government', 'take', 'change', 'one', 'gallon', 'gas', '80'] 

What's up? I would like to know how the Arab is doing.
['would', 'like', 'know', 'arab'] 

I am listening to radio wa in jacmel. I am asking for help to remove the dead bodies under La trinite college situated at university inasmo. The dead bodies are those of students and teachers
['listening', 'radio', 'wa', 'jacmel', 'asking', 'help', 'remove', 'dead', 'body', 'la', 'trinite', 'college', 'situated', 'university', 'inasmo', 'dead', 'body', 'student', 'teacher'] 

In which transfert house does someone abr

We are about 500 people. We're in Martissant 23, Village Dantes. God bless you.
['500', 'people', 'martissant', '23', 'village', 'dante', 'god', 'bless'] 

Digicel let me go through, it's an emergency
['digicel', 'let', 'go', 'emergency'] 

Where can I find Capital Bank please?
['find', 'capital', 'bank', 'please'] 

We are in Plaine du Cul-de-sac. Where's the nearest food distribution?
['plaine', 'du', 'cul', 'de', 'sac', 'nearest', 'food', 'distribution'] 

I am listening to Radio Dabon. We need help and doctors in that area. We are unable to move around because we have no gas. Dabon is located close to Leogane.
['listening', 'radio', 'dabon', 'need', 'help', 'doctor', 'area', 'unable', 'move', 'around', 'gas', 'dabon', 'located', 'close', 'leogane'] 

The message might be saying that they have been stuck in the presidential palace ( pal ) since the same Tuesday ( as the quake ). They need water. The message says they are not finding a little water. No names, no number of people give

Is it true that the political city will held in Hinche?
['true', 'political', 'city', 'held', 'hinche'] 

in what field would you need me to speak creole. French, half english, ( MW? )
['field', 'would', 'need', 'speak', 'creole', 'french', 'half', 'english', 'mw'] 

unrecognized characterse initial formation accelerated, organized by MENFP, financed by BID, launched in truncated
['unrecognized', 'characterse', 'initial', 'formation', 'accelerated', 'organized', 'menfp', 'financed', 'bid', 'launched', 'truncated'] 

continues previous truncated message : regarding education for all
['continues', 'previous', 'truncated', 'message', 'regarding', 'education'] 

Bizoton desperately needs help. We are humiliated.
['bizoton', 'desperately', 'need', 'help', 'humiliated'] 

Where can I find a car to leave in?
['find', 'car', 'leave'] 

Hello Good Morning We live on 31 Delmas we are without water without food and what we had have finished Please do something for us!
['hello', 'good', 'morning',

Road off of 200/2 to south of central Leogane. Same road that goes to Sabouce ends at Deslandes. No GPS coordinates available from here.
['road', '200', '2', 'south', 'central', 'leogane', 'road', 'go', 'sabouce', 'end', 'deslandes', 'gps', 'coordinate', 'available'] 

miques, antihitamines, diapers, folic acid, antifungus, vitamin C, feminine pads, vaginal solutions, klorox, disinfectants.. 
['miques', 'antihitamines', 'diaper', 'folic', 'acid', 'antifungus', 'vitamin', 'c', 'feminine', 'pad', 'vaginal', 'solution', 'klorox', 'disinfectant'] 

Hygienic . .. , mobile toilets, batteries, generators, DLO? toiletries, clothes, linens, underwear. .. 289 women, 181 men
['hygienic', 'mobile', 'toilet', 'battery', 'generator', 'dlo', 'toiletry', 'clothes', 'linen', 'underwear', '289', 'woman', '181', 'men'] 

taking our case into consideration, movement of peasants ( cane ) from Deslands. .. . please advise
['taking', 'case', 'consideration', 'movement', 'peasant', 'cane', 'deslands', 'please

...

The South African National Defence Force (SANDF) has four helicopter and two fixed wing planes which are amongst the 24 being funded by WFP.
['south', 'african', 'national', 'defence', 'force', 'sandf', 'four', 'helicopter', 'two', 'fixed', 'wing', 'plane', 'amongst', '24', 'funded', 'wfp'] 

A UNITA deserter alleged this week that Savimbi's calls for "dialogue" were simply a bluff to gain time and rearm his forces.
['unita', 'deserter', 'alleged', 'week', 'savimbi', 'call', 'dialogue', 'simply', 'bluff', 'gain', 'time', 'rearm', 'force'] 

The government declared the outbreak a national health emergency and mobilised partners to conduct additional polio vaccination campaigns in Upper Nile, Jonglei, Eastern Equatoria, Central Equatoria and Unity states that were considered most at risk.
['government', 'declared', 'outbreak', 'national', 'health', 'emergency', 'mobilised', 'partner', 'conduct', 'additional', 'polio', 'vaccination', 'campaign', 'upper', 'nile', 'jonglei', 'eastern', 'equ

"The pattern is always the same: steal, loot, and then set fire to everything," says the interlocutor to Misna adding that "an armed uprising is, at present, the only way for people to regain their dignity trampled by a government that is illiberal and violent."
['pattern', 'always', 'steal', 'loot', 'set', 'fire', 'everything', 'say', 'interlocutor', 'misna', 'adding', 'armed', 'uprising', 'present', 'way', 'people', 'regain', 'dignity', 'trampled', 'government', 'illiberal', 'violent'] 

Sirajganj, Bangladesh. When the rain-swollen Jamuna River breached its banks and inundated Sirajganj town 4 years ago, the streets were under knee-deep water, forcing shutdowns of businesses and schools.
['sirajganj', 'bangladesh', 'rain', 'swollen', 'jamuna', 'river', 'breached', 'bank', 'inundated', 'sirajganj', 'town', '4', 'year', 'ago', 'street', 'knee', 'deep', 'water', 'forcing', 'shutdown', 'business', 'school'] 

Damage to the Nacala rail corridor by the rains has delayed expected arrivals a

Residents were caught by surprise by the sheer force of the waters, which ripped up pavements and traffic lights and flooded buildings.
['resident', 'caught', 'surprise', 'sheer', 'force', 'water', 'ripped', 'pavement', 'traffic', 'light', 'flooded', 'building'] 

Officials said they would begin taking a census of people in camps on Feb. 1 to determine who gets to move to barracks first, where there will be communal kitchens and schools.
['official', 'said', 'would', 'begin', 'taking', 'census', 'people', 'camp', 'feb', '1', 'determine', 'get', 'move', 'barrack', 'first', 'communal', 'kitchen', 'school'] 

Despite their territorial losses, the insurgents have kept up their deadly raids, explosions and suicide attacks on "soft" targets such as markets and mosques.
['despite', 'territorial', 'loss', 'insurgent', 'kept', 'deadly', 'raid', 'explosion', 'suicide', 'attack', 'soft', 'target', 'market', 'mosque'] 

Other essential items distributed by ADRA include pots, plates, cups and cutle

UNHCR ($653,000) is supplying basic non-food items (such as sanitary kits, mosquito nets, kettles, and pots) and tents to returnees whose transfer to their original villages it is also organising.
['unhcr', '653', '000', 'supplying', 'basic', 'non', 'food', 'item', 'sanitary', 'kit', 'mosquito', 'net', 'kettle', 'pot', 'tent', 'returnees', 'whose', 'transfer', 'original', 'village', 'also', 'organising'] 

In addition, there are two outpatient clinics and a half dozen health posts in various outlying districts.When the matter had been debated previously, the Non-Aligned Movement foreign ministers firmly stated that there was no right to humanitarian intervention.
['addition', 'two', 'outpatient', 'clinic', 'half', 'dozen', 'health', 'post', 'various', 'outlying', 'district', 'matter', 'debated', 'previously', 'non', 'aligned', 'movement', 'foreign', 'minister', 'firmly', 'stated', 'right', 'humanitarian', 'intervention'] 

The political forces in the region must be alert to the phenome

The World Health Organization and Norway gathered the world's leading experts on vaccine trials for a planning meeting in November.
['world', 'health', 'organization', 'norway', 'gathered', 'world', 'leading', 'expert', 'vaccine', 'trial', 'planning', 'meeting', 'november'] 

The ability to pick dengue from influenza is crucial, as dengue can progress into a more serious illness called Dengue Haemorrhagic Fever (DHF).
['ability', 'pick', 'dengue', 'influenza', 'crucial', 'dengue', 'progress', 'serious', 'illness', 'called', 'dengue', 'haemorrhagic', 'fever', 'dhf'] 

A Federation chartered ship arrived from Lae with relief supplies which were quickly unloaded in Aitape.
['federation', 'chartered', 'ship', 'arrived', 'lae', 'relief', 'supply', 'quickly', 'unloaded', 'aitape'] 

The result is that in Aceh province many prefabricated shelters are now unhealthy, while a large number of survivors continue to live in them.
['result', 'aceh', 'province', 'many', 'prefabricated', 'shelter', 'u

In [23]:
def display_results(y_test, y_pred):
    """[summary]
    
    Arguments:
        y_test {[type]} -- [description]
        y_pred {[type]} -- [description]
    """
    labels = np.unique(y_pred)
    confusion_mat = confusion_matrix(y_test, y_pred, labels=labels)
    accuracy = (y_pred == y_test).mean()

    print("Labels:", labels)
    print("Confusion Matrix:\n", confusion_mat)
    print("Accuracy:", accuracy)


### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [9]:
pipeline = Pipeline([
    ('vect', CountVectorizer(tokenizer=tokenize)),
    ('tfidf', TfidfTransformer()),
    ('clf', MultiOutputClassifier(RandomForestClassifier(random_state=42))),
    ])


### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [17]:
X_train, X_test, y_train, y_test = train_test_split(X, y)

In [25]:
X_train.head()

11879    The ISS will pass over Santiago at mag -0.8 at...
13862    BANDA ACEH, Indonesia, Dec 15 (Reuters) - The ...
10641    If anyone is having a Hurricane Sandy costume ...
383      The people cannot find food, hunger is killing...
3789            We have a problem with Registre in Akaye. 
Name: message, dtype: object

In [21]:
pipeline.fit(X_train, y_train)

/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.

/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Users/jaywang/anaconda3/envs/data_science/lib/python3.7/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.

Pipeline(memory=None,
         steps=[('vect',
                 CountVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.int64'>, encoding='utf-8',
                                 input='content', lowercase=True, max_df=1.0,
                                 max_features=None, min_df=1,
                                 ngram_range=(1, 1), preprocessor=None,
                                 stop_words=None, strip_accents=None,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=<function tokenize at...
                 MultiOutputClassifier(estimator=RandomForestClassifier(bootstrap=True,
                                                                        class_weight=None,
                                                                        criterion='gini',
                                                                  

In [ ]:
# Predict on test data
y_pred = pipeline.predict(X_test)

In [22]:
# Display results
display_results(y_test, y_pred)

ValueError: multiclass-multioutput is not supported

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

### 6. Improve your model
Use grid search to find better parameters. 

In [ ]:
parameters = 

cv = 

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

### 9. Export your model as a pickle file

### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.